# 1. Entendimiento de los datos

Primero se va a revisar el conjunto de datos para ver si hay suficientes entradas para utilizar los algoritmos de agrupamiento con los cuales se buscará solucionar el problema. Una vez se demuestre que se tienen los datos suficientes se buscará entender los diferentes valores que hay para las distintas columnas

Para la carga y manipulación de datos se utiliza la libreria Pandas (https://pandas.pydata.org/) y para la visualización Matplotlib (https://matplotlib.org/) y Seaborn (https://seaborn.pydata.org/). Primero se realiza la instalación de las librerias necesarias.

In [1]:
pip install ydata-profiling

Note: you may need to restart the kernel to use updated packages.


In [2]:
# Librería para comando de sistema
import os

# Librerías para manejo de datos
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import ydata_profiling

# Librerías de aprendizaje automático.
# Para realizar la separación del conjunto de aprendizaje en entrenamiento y test.
from sklearn.model_selection import train_test_split

# Para construir un modelo con el algoritmo de regresión lineal
from sklearn.linear_model import LinearRegression

# Para determinar el rendimiento del modelo con las métricas MSE, MAE y R2
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

# Para sacar un reporte estadístico que podemos usar para determinar las importancia de las variables explicativas.
import statsmodels.api as sm 

#Librerias para la transformación de los datos
from sklearn.preprocessing import StandardScaler, OneHotEncoder

# Librerias para pipelines
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import FunctionTransformer
from sklearn.compose import ColumnTransformer

# Librerias para el simple imputer
from sklearn.impute import SimpleImputer

Despues de haber importado las librerias que nos serviran para realizar todo durante el notebook hacemos la carga de los datos de entrenamiento y los de prueba

In [3]:
# Full data son los datos que usaremos para entrenar el modelo
full_data = pd.read_csv('data/data.csv', sep=',', encoding = 'utf-8')

# Test data son los datos usados para probar nuestro modelo
test_data = pd.read_csv('data/data_test.csv', sep=',', encoding = 'utf-8')

In [4]:
# Obtenemos las filas y las columnas de nuestro dataframe
full_data.shape

(7115, 12)

In [5]:
# Almacenamos en una variable para poder realizar todo lo que neceistamos
motoralpes = full_data

In [6]:
# Obtenemos la informacion de los datos
motoralpes.info

<bound method DataFrame.info of       Unnamed: 0    year  km_driven                 owner seller_type  seats  \
0              0     NaN   145500.0                   NaN  Individual    5.0   
1              1  2014.0   120000.0          Second Owner  Individual    5.0   
2              2  2006.0   140000.0           Third Owner  Individual    5.0   
3              3  2010.0   127000.0           First Owner  Individual    5.0   
4              4  2007.0   120000.0           First Owner  Individual    5.0   
...          ...     ...        ...                   ...         ...    ...   
7110        8123  2013.0   110000.0           First Owner  Individual    5.0   
7111        8124  2007.0   119000.0  Fourth & Above Owner  Individual    5.0   
7112        8125  2009.0   120000.0           First Owner  Individual    5.0   
7113        8126  2013.0    25000.0           First Owner  Individual    5.0   
7114        8127  2013.0    25000.0           First Owner  Individual    5.0   

       

In [7]:
# Por ultimo visualizamos los datos usando ydata-profiling
profile = ydata_profiling.ProfileReport(motoralpes)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# 2. Identificacion de variables a utilizar

Con la visualizacion anterior sabemos que tenemos 12 variables de las cuales debemos quitar 1 que se llama `Unnamed: 0` porque corresponde a los indices de los datos. De resto usaremos todas las columnas para experimentar e iremos quitando a medida de que lo vayamos considerando

# 3. Preparacion de los datos

Para la preparacion de los datos usaremos pipelines. Esto nos servira para que cuando queramos experimentar con otras columnas podamos realizar esta preparacion rapidamente.

In [8]:
# Veremos los datos que tenemos para realizar las transformaciones necesarias
motoralpes.dtypes

Unnamed: 0         int64
year             float64
km_driven        float64
owner             object
seller_type       object
seats            float64
fuel              object
transmission      object
mileage          float64
engine           float64
max_power        float64
selling_price    float64
dtype: object

Como ahora sabes que tipos de datos tenemos. Vamos a consultar la cantida de nulos para conocer el tipo ed transformaciones que tenemos que hacer. En este punto como vamos a usar todas las columnas lo primero que haremos es convertir las varibales categoricas a numericas. Esto implica usar el OneHotEncoder para crear variables binarias en columnas que representen un dato. Tambien reemplazaremos los datos de Owner por numero secenciales, esto porque tienen una relacion secuencial. Se hacen estas transformaciones primero porque pueden generar nuevos valores nulos. Luego, imputaremos con el metodo de la media en los nulos para las variables numericas que no necesiten un entero. 

In [9]:
# Esto nos permite conocer el tipo de transformaciones que le debemos hacer a los datos numericos
motoralpes.isna().sum()

Unnamed: 0         0
year             239
km_driven        198
owner            239
seller_type        0
seats              0
fuel               0
transmission       0
mileage          198
engine           280
max_power        268
selling_price    401
dtype: int64

In [10]:
#Le aplicaremos una transformacion a las variables categoricas
categoric = ['fuel','transmission']

cateNumPipe = Pipeline([
    ("onehot", OneHotEncoder())
])

# Hacemos un cambio de variable categorica a numerica reemplazando valores a la columna 'Owner'
def replace_values(X):
    X["owner"].replace(['Test Drive Car', 'First Owner', 'Second Owner', 'Third Owner', 'Fourth & Above Owner'],[0, 1, 2, 3, 4], inplace=True)

changeOwnerPipe = Pipeline([
    ("change", FunctionTransformer(replace_values))
])

# Ahora imputamos con el metodo de la media a los valores que tienen nulos
meanImp = ['km_driven', 'mileage', 'max_power','selling_price']
mostFImp = ['year','owner','engine']

numImpPipeMe = Pipeline([
    ("imputerMean", SimpleImputer(strategy="mean")),
])

numImpPipeMo = Pipeline([
    ("imputerMostF", SimpleImputer(strategy="most_frequent"))
])

Ahora realizaremos el preprocesamiento y limpieza de los datos utilizando pipelines

# 4. Modelamiento

# 5. Evaluacion cuantitativa

### 5.1 Recomendamos instalar el modelo de estimacion?

### 5.2 Que posibilidades tiene la empresa?

# 6. Evaluacion Cualitativa

### 6.1 Validacion de supuestos

### 6.2 Interpretacion de coeficientes

# 7. Visualizar el resultado del modelo

# 8. Exportar el modelo